#### Attempt to map the conditions and interventions to CURIEs

In [337]:
import pandas as pd
import requests
import bs4
from bs4 import BeautifulSoup
import re
import collections
import os
import json
import numpy as np
import time
import pickle
from multiprocessing.pool import ThreadPool
import multiprocessing
from functools import reduce


In [2]:
%pip install thefuzz
from thefuzz import fuzz # fuzzy matching explained: https://www.datacamp.com/tutorial/fuzzy-string-python

Note: you may need to restart the kernel to use updated packages.


In [3]:
# for testing
data_extracted = "/Users/Kamileh/Work/ISB/NCATS_BiomedicalTranslator/Projects/ClinicalTrials/ETL_Python/data/2023-04-03_extracted"


In [4]:
# read in pipe-delimited files
conditions_df = pd.read_csv(data_extracted + '/conditions.txt', sep='|', index_col=False, header=0)
interventions_df = pd.read_csv(data_extracted + '/interventions.txt', sep='|', index_col=False, header=0)
browse_conditions_df = pd.read_csv(data_extracted + '/browse_conditions.txt', sep='|', index_col=False, header=0)
browse_interventions_df = pd.read_csv(data_extracted + '/browse_interventions.txt', sep='|', index_col=False, header=0)

browse_interventions_df.head()

id       nct_id          mesh_term downcase_mesh_term      mesh_type
0  57856435  NCT00246285        Risperidone        risperidone      mesh-list
1  57856584  NCT04626778  Hydrogen Peroxide  hydrogen peroxide      mesh-list
2  57856732  NCT00219908       Mitoxantrone       mitoxantrone      mesh-list
3  57856807  NCT00220064           Vitamins           vitamins  mesh-ancestor
4  57857560  NCT04612894           Apatinib           apatinib      mesh-list

In [5]:
interventions_df.head()

id       nct_id intervention_type            name  \
0  31893754  NCT00371085        Behavioral       education   
1  31741354  NCT01604265              Drug         Placebo   
2  31741355  NCT01604265              Drug         Sativex   
3  31893755  NCT00551759              Drug  5-Fluorouracil   
4  31893756  NCT00551759              Drug     Oxaliplatin   

                                         description  
0  Video-based educational program for heart fail...  
1  Contained peppermint oil, 0.05% (v/v), quinoli...  
2  Contained delta-9-tetrahydrocannabinol (THC), ...  
3                                           given IV  
4                                           given IV

In [6]:
browse_conditions_df.head()
browse_conditions = browse_conditions_df[["nct_id", "downcase_mesh_term", "mesh_type"]]

In [7]:
# every clinical trial has at least one MeSH-list (leaf), and may have 0 or more MeSH-ancestors (see MeSH analytics script)
# subset browse_conditions to get only the MeSH-list terms or leaves
condition_mesh_leaves = browse_conditions_df[browse_conditions_df["mesh_type"].str.contains("mesh-list")]
condition_mesh_leaves


id       nct_id             mesh_term    downcase_mesh_term  \
0        113697939  NCT00185796              Syndrome              syndrome   
2        113698185  NCT03516604            Depression            depression   
5        113698730  NCT00461539            Depression            depression   
6        113698920  NCT05324137                Polyps                polyps   
11       113700140  NCT00176514             Mucositis             mucositis   
...            ...          ...                   ...                   ...   
2849547  111234990  NCT00733525       Bulimia Nervosa       bulimia nervosa   
2849551  111234994  NCT02653131  Short Bowel Syndrome  short bowel syndrome   
2849552  111234995  NCT02653131              Syndrome              syndrome   
2849564  111204205  NCT04834908            Infections            infections   
2849565  111204206  NCT04834908              COVID-19              covid-19   

         mesh_type  
0        mesh-list  
2        mesh-list  
5        mesh-list  
6        mesh-list  
11       mesh-list  
...            ...  
2849547  mesh-list  
2849551  mesh-list  
2849552  mesh-list  
2849564  mesh-list  
2849565  mesh-list  

[761406 rows x 5 columns]

In [8]:
conditions_unmapped = conditions_df[["nct_id", "downcase_name"]]
conditions_unmapped

nct_id              downcase_name
0       NCT01819987                 overweight
1       NCT01821599             rehabilitation
2       NCT01823731             ovarian cancer
3       NCT01825850                    healthy
4       NCT01829022                      myoma
...             ...                        ...
771537  NCT00323960   juvenile dermatomyositis
771538  NCT00323037   congestive heart failure
771539  NCT00246857  primary immune deficiency
771540  NCT00128297              breast cancer
771541  NCT00128297        neoplasm metastasis

[771542 rows x 2 columns]

In [9]:
# some conditions have a MESH term match, even if it doesn't show up in the same clinical trial
# add those matches based on MESH term alone (irrespective of clinical trial)
len(browse_conditions.downcase_mesh_term.unique())

4315

In [10]:
# map any matching MESH term condition to the conditions 
all_mesh_conditions = browse_conditions.downcase_mesh_term.unique()
mask = np.isin(conditions_unmapped['downcase_name'], all_mesh_conditions)
conditions_unmapped['mesh_conditions_exact_mapped'] = np.where(mask, conditions_unmapped['downcase_name'], np.nan)

with pd.option_context("display.max_rows", 30000):
    display(conditions_unmapped[700:1000])

/var/folders/49/18qlr0bn7xg_mk2pzxvrb0f80000gn/T/ipykernel_29386/3037061082.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  conditions_unmapped['mesh_conditions_exact_mapped'] = np.where(mask, conditions_unmapped['downcase_name'], np.nan)


nct_id                                      downcase_name  \
700  NCT00222703                                   chronic diseases   
701  NCT00222703                               tobacco use disorder   
702  NCT00222742                             traumatic brain injury   
703  NCT00086073                                  parkinson disease   
704  NCT02968043                    scoliosis idiopathic adolescent   
705  NCT00222781                                           diabetes   
706  NCT00222781                                            obesity   
707  NCT00222820                                   major depression   
708  NCT00222859                                     hiv infections   
709  NCT00061724                            gastroesophageal reflux   
710  NCT00222898                                    pancreatic cyst   
711  NCT00222898                              pancreatic pseudocyst   
712  NCT00222898                                pancreatic neoplasm   
713  NCT01819974          patients in highest medication error risk   
714  NCT01820000                                       heart attack   
715  NCT01820013                                        pelvic pain   
716  NCT01820013                        symphysis pubis dysfunction   
717  NCT01820026                                          cirrhosis   
718  NCT01820039  unexplained subfertile couples with a good pro...   
719  NCT01820052                               primary fibromyalgia   
720  NCT01820065  posterior capsule opacification after phacoemu...   
721  NCT01820078                chronic kidney disease, unspecified   
722  NCT01820091                         non-small cell lung cancer   
723  NCT01820104                                            healthy   
724  NCT01820117                                   hodgkin lymphoma   
725  NCT01820130                                      heart failure   
726  NCT01820143                                            healthy   
727  NCT01820143                                   pharmacokinetics   
728  NCT01820143                                   pharmacodynamics   
729  NCT01820143                                         ilaprazole   
730  NCT01820156                   obstructive sleep apnea syndrome   
731  NCT01820169                                           diabetes   
732  NCT01820182                                             anemia   
733  NCT01820182                         gastrointestinal bleedings   
734  NCT01820182                                             méléna   
735  NCT01820182                                     angiodysplasia   
736  NCT01820182                                             polyps   
737  NCT01820195                     chronic kidney disease stage 2   
738  NCT01820195            radiographic contrast agent nephropathy   
739  NCT01820208                         severe alcoholic hepatitis   
740  NCT01820221                                            obesity   
741  NCT01820221                                          pregnancy   
742  NCT01820234                                        skin cancer   
743  NCT01820234                                          screening   
744  NCT01820234                                       telemedicine   
745  NCT01820247                                    crohn's disease   
746  NCT01820273                                    type 2 diabetes   
747  NCT01820273                                            obesity   
748  NCT01820286                                   bipolar disorder   
749  NCT01820286                                         depression   
750  NCT01820299                                      solid cancers   
751  NCT01820312       squamous cell carcinoma of the head and neck   
752  NCT01820325                        non-small cell lunch cancer   
753  NCT01820338                                            obesity   
754  NCT01820351  assessment of muscle architecture and tendon a...   
755  NCT01820377                  

In [11]:
# make a dict of mapped terms
conditions_mesh_exact_mapped = conditions_unmapped[~conditions_unmapped['mesh_conditions_exact_mapped'].isnull()] # get the rows where mesh_term is empty bc there was no match there
# conditions_mesh_exact_mapped = conditions_mesh_exact_mapped.drop_duplicates(['downcase_name']).sort_index()

# mesh_condition_dict = {}

In [12]:
conditions_unmapped = conditions_unmapped[conditions_unmapped['mesh_conditions_exact_mapped'].isnull()] # get the rows where mesh_term is empty bc there was no match there
conditions_unmapped = conditions_unmapped.drop('mesh_conditions_exact_mapped', axis=1) # drop the empty column now

conditions_unmapped

nct_id              downcase_name
1       NCT01821599             rehabilitation
2       NCT01823731             ovarian cancer
3       NCT01825850                    healthy
5       NCT01838148                      spect
7       NCT01841983                      sleep
...             ...                        ...
771528  NCT00413998       mitral regurgitation
771537  NCT00323960   juvenile dermatomyositis
771538  NCT00323037   congestive heart failure
771539  NCT00246857  primary immune deficiency
771540  NCT00128297              breast cancer

[545877 rows x 2 columns]

## Use fuzzy string matching to get MESH terms matches that are identical to downcase_name, but rearranged

In [13]:
# fuzzy matching explained: https://www.datacamp.com/tutorial/fuzzy-string-python

def get_token_sort_ratio(str1, str2):
    try:
        return fuzz.token_sort_ratio(str1, str2)
    except:
        return None
    
sort_ratio = np.vectorize(get_token_sort_ratio)

def get_token_set_ratio(str1, str2):
    try:
        return fuzz.token_set_ratio(str1, str2)
    except:
        return None  
set_ratio = np.vectorize(get_token_set_ratio)

def get_similarity_score(str1, str2):
    try:
        return fuzz.ratio(str1, str2)
    except:
        return None
sim_score = np.vectorize(get_similarity_score)



In [14]:
mesh_conditions_per_study = pd.DataFrame(browse_conditions[["nct_id", "downcase_mesh_term", "mesh_type"]].groupby("nct_id")["downcase_mesh_term"].apply(list))
with pd.option_context("max_colwidth", None):
    display(mesh_conditions_per_study[:30])


downcase_mesh_term
nct_id                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         
NCT00000102                                                                                                                                                      [adrenal hyperplasia, congenital, adrenogenital syndrome, adrenocortical hyperfunction, hyperplasia, pathologic processes, disorders of sex development, urogenital abnormalities, congenital abnormalities, genetic diseases, inborn, steroid metabolism, inborn errors, metabolism, inborn errors, metabolic diseases, adrenal gland diseases, endocrine system diseases, gonadal disorders]
NCT00000104                                                                                                                                                                                                                                                                                                                                                                                                                                                                    [poisoning, lead poisoning, chemically-induced disorders, heavy metal poisoning]
NCT00000105                                                                                                                                                                                                                                                                                                                                                                                                           [tetanus, clostridium infections, gram-positive bacterial infections, bacterial infections, bacterial infections and mycoses, infections]
NCT00000106                                                                                                                                                                                                                                                                                                                                                                                                                                                       [rheumatic diseases, collagen diseases, musculoskeletal diseases, connective tissue diseases]
NCT00000107                                                                                                                                                                                                                                                                                                                                                                                                                        [heart defects, congenital, congenital abnormalities, heart diseases, cardiovascular diseases, cardiovascular abnormalities]
NCT00000108                                                                                                                                                                                                                                                                                                                                                                                                                                                 [cardiovascular diseases, coronary disease, myocardial ischemia, heart diseases, vascular diseases]
NCT00000111                                                                                                                                                                  

In [15]:
print(len(conditions_unmapped.downcase_name.unique()))
conditions_unmapped

99160


nct_id              downcase_name
1       NCT01821599             rehabilitation
2       NCT01823731             ovarian cancer
3       NCT01825850                    healthy
5       NCT01838148                      spect
7       NCT01841983                      sleep
...             ...                        ...
771528  NCT00413998       mitral regurgitation
771537  NCT00323960   juvenile dermatomyositis
771538  NCT00323037   congestive heart failure
771539  NCT00246857  primary immune deficiency
771540  NCT00128297              breast cancer

[545877 rows x 2 columns]

In [16]:
conditions_unmapped_all_mesh_terms = pd.merge(conditions_unmapped, 
                                                mesh_conditions_per_study,
                                                how='left',
                                                left_on=['nct_id'],
                                                right_on = ['nct_id'])

# some clinical trials are missing from browse_conditions (those nct_ids are not present in the browse_conditions text) They have NaN in the downcase_mesh_term column
conditions_unmapped_all_mesh_terms = conditions_unmapped_all_mesh_terms[~conditions_unmapped_all_mesh_terms['downcase_mesh_term'].isnull()] # subset or delete rows where either column is empty/Nonetype bc fuzzymatching functions will throw error if handling
conditions_unmapped_all_mesh_terms


nct_id              downcase_name  \
1       NCT01823731             ovarian cancer   
3       NCT01838148                      spect   
5       NCT01846520              ureter cancer   
7       NCT02985749                        pdd   
9       NCT01865357                  brain mri   
...             ...                        ...   
545872  NCT00413998       mitral regurgitation   
545873  NCT00323960   juvenile dermatomyositis   
545874  NCT00323037   congestive heart failure   
545875  NCT00246857  primary immune deficiency   
545876  NCT00128297              breast cancer   

                                       downcase_mesh_term  
1       [ovarian neoplasms, carcinoma, ovarian epithel...  
3       [coronary artery disease, myocardial ischemia,...  
5       [carcinoma, pancreatic neoplasms, sarcoma, sto...  
7       [disease, autistic disorder, autism spectrum d...  
9       [multiple sclerosis, syndrome, sclerosis, dise...  
...                                                   ...  
545872  [coronary artery disease, mitral valve insuffi...  
545873  [dermatomyositis, polymyositis, myositis, musc...  
545874  [heart failure, heart diseases, cardiovascular...  
545875  [genetic diseases, inborn, primary immunodefic...  
545876  [breast neoplasms, neoplasm metastasis, neopla...  

[448886 rows x 3 columns]

In [17]:
conditions_unmapped_all_mesh_terms = conditions_unmapped_all_mesh_terms.explode('downcase_mesh_term')
conditions_unmapped_all_mesh_terms

nct_id   downcase_name             downcase_mesh_term
1       NCT01823731  ovarian cancer              ovarian neoplasms
1       NCT01823731  ovarian cancer  carcinoma, ovarian epithelial
1       NCT01823731  ovarian cancer      endocrine gland neoplasms
1       NCT01823731  ovarian cancer              neoplasms by site
1       NCT01823731  ovarian cancer                      neoplasms
...             ...             ...                            ...
545876  NCT00128297   breast cancer                      neoplasms
545876  NCT00128297   breast cancer                breast diseases
545876  NCT00128297   breast cancer                  skin diseases
545876  NCT00128297   breast cancer           neoplastic processes
545876  NCT00128297   breast cancer           pathologic processes

[5176844 rows x 3 columns]

In [18]:
conditions_unmapped_all_mesh_terms = conditions_unmapped_all_mesh_terms[~conditions_unmapped_all_mesh_terms['downcase_mesh_term'].isnull()] # subset or delete rows where either column is empty/Nonetype bc fuzzymatching functions will throw error if handling
print(len(conditions_unmapped_all_mesh_terms))

conditions_unmapped_all_mesh_terms["sort_ratio"] = sort_ratio(conditions_unmapped_all_mesh_terms[["downcase_mesh_term"]].values, conditions_unmapped_all_mesh_terms[["downcase_name"]].values)
# conditions_unmapped_all_mesh_terms["set_ratio"] = set_ratio(conditions_unmapped_all_mesh_terms[["downcase_mesh_term"]].values, conditions_unmapped_all_mesh_terms[["downcase_name"]].values)
conditions_unmapped_all_mesh_terms["sim_score"] = sim_score(conditions_unmapped_all_mesh_terms[["downcase_mesh_term"]].values, conditions_unmapped_all_mesh_terms[["downcase_name"]].values)

conditions_unmapped_all_mesh_terms


5176844


nct_id   downcase_name             downcase_mesh_term  \
1       NCT01823731  ovarian cancer              ovarian neoplasms   
1       NCT01823731  ovarian cancer  carcinoma, ovarian epithelial   
1       NCT01823731  ovarian cancer      endocrine gland neoplasms   
1       NCT01823731  ovarian cancer              neoplasms by site   
1       NCT01823731  ovarian cancer                      neoplasms   
...             ...             ...                            ...   
545876  NCT00128297   breast cancer                      neoplasms   
545876  NCT00128297   breast cancer                breast diseases   
545876  NCT00128297   breast cancer                  skin diseases   
545876  NCT00128297   breast cancer           neoplastic processes   
545876  NCT00128297   breast cancer           pathologic processes   

        sort_ratio  sim_score  
1               65         65  
1               57         42  
1               31         41  
1               32         26  
1               35         17  
...            ...        ...  
545876          27         27  
545876          64         64  
545876          38         31  
545876          42         42  
545876          30         30  

[5176844 rows x 5 columns]

In [19]:
conditions_mesh_fuzz_scored = conditions_unmapped_all_mesh_terms[(conditions_unmapped_all_mesh_terms['sim_score'] > 88) | (conditions_unmapped_all_mesh_terms['sort_ratio'] > 88)]
conditions_mesh_fuzz_scored = conditions_mesh_fuzz_scored.sort_values(by = ['nct_id', 'downcase_name'], ascending = [True, True], na_position = 'first')

conditions_mesh_fuzz_scored

nct_id                          downcase_name  \
17708   NCT00000102         congenital adrenal hyperplasia   
191694  NCT00000126              ischemic optic neuropathy   
172984  NCT00000127              ischemic optic neuropathy   
191695  NCT00000132                    open-angle glaucoma   
20691   NCT00000140        proliferative vitreoretinopathy   
...             ...                                    ...   
332368  NCT05793684                obstructive sleep apnea   
332366  NCT05793697  chronic obstructive pulmonary disease   
332350  NCT05793827                 traumatic brain injury   
332333  NCT05793983                       cirrhosis, liver   
332335  NCT05793983        liver failure, acute on chronic   

                            downcase_mesh_term  sort_ratio  sim_score  
17708          adrenal hyperplasia, congenital         100         62  
191694              optic neuropathy, ischemic         100         63  
172984              optic neuropathy, ischemic         100         63  
191695                    glaucoma, open-angle         100         51  
20691         vitreoretinopathy, proliferative         100         54  
...                                        ...         ...        ...  
332368                sleep apnea, obstructive         100         47  
332366  pulmonary disease, chronic obstructive         100         51  
332350               brain injuries, traumatic          91         47  
332333                         liver cirrhosis         100         58  
332335          acute-on-chronic liver failure         100         46  

[75567 rows x 5 columns]

In [20]:
conditions_mesh_fuzz_scored = conditions_mesh_fuzz_scored.sort_values('sort_ratio', ascending=False).drop_duplicates(['nct_id', 'downcase_name']).sort_index() # there may be many mesh terms that past the ratio and score filter; this causes duplicates bc I exploded the df...this line of code picks one and throws away other potential matches for one disease-nct_id pair
conditions_mesh_fuzz_scored = conditions_mesh_fuzz_scored.sort_values(['nct_id'], ascending=False)
print(len(conditions_mesh_fuzz_scored))

with pd.option_context("display.max_rows", 30000):
    display(conditions_mesh_fuzz_scored[:3000])
    

73181


nct_id                                      downcase_name  \
332335  NCT05793983                    liver failure, acute on chronic   
332333  NCT05793983                                   cirrhosis, liver   
332350  NCT05793827                             traumatic brain injury   
332366  NCT05793697              chronic obstructive pulmonary disease   
332368  NCT05793684                            obstructive sleep apnea   
332403  NCT05793268                                chronic hepatitis b   
332412  NCT05793190                            alcoholic liver disease   
332418  NCT05793151              head and neck squamous cell carcinoma   
332425  NCT05793125                          hypertension in pregnancy   
332448  NCT05792878                                chronic hepatitis b   
332451  NCT05792839                                   abdominal hernia   
332453  NCT05792813                                   male infertility   
332455  NCT05792800                                      caries,dental   
332456  NCT05792787                               apical periodontitis   
332472  NCT05792527                               rheumatoid arthritis   
332474  NCT05792501              ventilator associated pneumonia (vap)   
332484  NCT05792358                             ankylosing spondylitis   
332487  NCT05792332                      msa - multiple system atrophy   
332495  NCT05792267                                 pancreatic disease   
332504  NCT05792215                                      caries,dental   
332515  NCT05792124                                 postoperative pain   
388894  NCT05791929                                         ulcer foot   
388898  NCT05791890                             acute myeloid leukemia   
388938  NCT05791799                       systemic lupus erythematosus   
388939  NCT05791786                            amniotic fluid embolism   
388940  NCT05791773                                knee osteoarthritis   
389000  NCT05791630                  labor (obstetrics)--complications   
436269  NCT05791526                                 ulcerative colitis   
389008  NCT05791487                                 ulcerative colitis   
389033  NCT05791435                                      pain, chronic   
389050  NCT05791149                       oral squamous cell carcinoma   
389058  NCT05791110                  pancreatic exocrine insufficiency   
332518  NCT05791032                            ventricular tachycardia   
436272  NCT05790889                                 malaria,falciparum   
389101  NCT05790824                                knee osteoarthritis   
389472  NCT05790395                          non communicable diseases   
389506  NCT05790278                             traumatic brain injury   
389512  NCT05790239                     post traumatic stress disorder   
532587  NCT05790083                                  atopic dermatitis   
532601  NCT05789966                             coronary heart disease   
532619  NCT05789641                                portal hypertension   
332541  NCT05789290                           temperature change, body   
532656  NCT05789069                               renal cell carcinoma   
532662  NCT05788991                                bacterial vaginosis   
532668  NCT05788939                                      skin neoplasm   
532700  NCT05788705                               rheumatoid arthritis   
532702  NCT05788679   mixed myelodysplastic/myeloproliferative disease   
532710  NCT05788549                                 ulcerative colitis   
533654  NCT05788302                     post traumatic stress disorder   
533655  NCT05788289                               mantle cell lymphoma   
533656  NCT05788211                                  cardiogenic shock   
544139  NCT05787951                                   myeloid leukemia   
544145  NCT05787860                              seborrheic dermatitis   
504528  NCT057877

In [21]:
### 100% reassortment score indicates that the mapped mesh term is probably correct bc liver failure, acute is considered identical to acute liver failure
### Look for examples where there reassorted (sort_ratio) score is high, but there is no comma, to see whether mappings are legitimate/my assumption that I can use high sort_ratio scores to call a mapping a near exact match is correct 
no_comma_reassortment_score_check = conditions_mesh_fuzz_scored[~conditions_mesh_fuzz_scored.astype(str).apply(lambda x: x.str.contains(','), axis=1).any(axis=1)]
no_comma_reassortment_score_check.to_csv('reassorted_high_no_comma.tsv', sep ='\t')
no_comma_reassortment_score_check

nct_id                          downcase_name  \
332418  NCT05793151  head and neck squamous cell carcinoma   
332456  NCT05792787                   apical periodontitis   
332487  NCT05792332          msa - multiple system atrophy   
332495  NCT05792267                     pancreatic disease   
388894  NCT05791929                             ulcer foot   
...             ...                                    ...   
140207  NCT00000574    acute respiratory distress syndrome   
21201   NCT00000572    acute respiratory distress syndrome   
16222   NCT00000538                   hyperlipoproteinemia   
21067   NCT00000530                      raynaud's disease   
16174   NCT00000142          cmv cytomegalovirus retinitis   

                              downcase_mesh_term  sort_ratio  sim_score  
332418  squamous cell carcinoma of head and neck          96         60  
332456                  periapical periodontitis          91         91  
332487                   multiple system atrophy          92         88  
332495                       pancreatic diseases          97         97  
388894                                foot ulcer         100         50  
...                                          ...         ...        ...  
140207             respiratory distress syndrome          91         91  
21201              respiratory distress syndrome          91         91  
16222                      hyperlipoproteinemias          98         98  
21067                            raynaud disease          94         94  
16174                  cytomegalovirus retinitis          93         93  

[28214 rows x 5 columns]

In [22]:
keys = list(conditions_mesh_fuzz_scored[["nct_id", "downcase_name"]].columns.values)
i1 = conditions_unmapped.set_index(keys).index
i2 = conditions_mesh_fuzz_scored.set_index(keys).index

print(len((conditions_df.downcase_name.unique())))
print(len(conditions_unmapped.downcase_name.unique()))
conditions_unmapped = conditions_unmapped[~i1.isin(i2)]
conditions_unmapped

102760
99160


nct_id              downcase_name
1       NCT01821599             rehabilitation
2       NCT01823731             ovarian cancer
3       NCT01825850                    healthy
5       NCT01838148                      spect
7       NCT01841983                      sleep
...             ...                        ...
771528  NCT00413998       mitral regurgitation
771537  NCT00323960   juvenile dermatomyositis
771538  NCT00323037   congestive heart failure
771539  NCT00246857  primary immune deficiency
771540  NCT00128297              breast cancer

[472696 rows x 2 columns]

In [23]:
conditions_unmapped

nct_id              downcase_name
1       NCT01821599             rehabilitation
2       NCT01823731             ovarian cancer
3       NCT01825850                    healthy
5       NCT01838148                      spect
7       NCT01841983                      sleep
...             ...                        ...
771528  NCT00413998       mitral regurgitation
771537  NCT00323960   juvenile dermatomyositis
771538  NCT00323037   congestive heart failure
771539  NCT00246857  primary immune deficiency
771540  NCT00128297              breast cancer

[472696 rows x 2 columns]

In [66]:
print(len(conditions_unmapped.downcase_name.unique()))
conditions_unmapped.downcase_name.unique()

94632


array(['rehabilitation', 'ovarian cancer', 'healthy', ...,
       'melanoma (excluding uveal melanoma)',
       'high energy midshaft clavicle fractures', 'vitamin d or placebo'],
      dtype=object)

In [32]:
def split_list(lst, sublist_length):
    return [lst[i:i+sublist_length] for i in range(0, len(lst), sublist_length)]

In [38]:
sublist_length = 990
conditions_unmapped_chunked = split_list(conditions_unmapped.downcase_name.unique(), sublist_length)

In [62]:
nr_url = 'https://name-resolution-sri.renci.org/lookup'
nr_terms = []
for chunk in conditions_unmapped_chunked:
    time.sleep(5)
    for term in chunk:
        nr_term = {}
        params = {'string':term, 'limit':1} # limit -1 makes this return all available equivalent CURIEs name resolver can give            
        r = requests.post(nr_url, params=params)
        try:
            res = r.json()
            if res:
                for key, val in res.items():
                    nr_term[term] = [key, val[0]]
                    nr_terms.append(nr_term)
            else:
                print(term + " unable to be mapped by Name Resolver")
        except Exception as e:
            print(e)
            print(term + " unable to be mapped by Name Resolver")
      

e03.155.197 unable to be mapped by Name Resolver
advanced solid tumors unable to be mapped by Name Resolver
locally advanced or metastatic digestive tract tumors unable to be mapped by Name Resolver
other solid tumors unable to be mapped by Name Resolver
need for tracheal tube exchange unable to be mapped by Name Resolver
primary total hip replacement (thr) unable to be mapped by Name Resolver
presence of post-extubation laryngeal oedema unable to be mapped by Name Resolver
any medical condition presented by patient unable to be mapped by Name Resolver
abdominothoracic surgery unable to be mapped by Name Resolver
village children unable to be mapped by Name Resolver
hospitalized smokers unable to be mapped by Name Resolver
patients in highest medication error risk unable to be mapped by Name Resolver
unexplained subfertile couples with a good prognosis. unable to be mapped by Name Resolver
posterior capsule opacification after phacoemulsification and iol implantation unable to be mappe

intracerebral infarcts unable to be mapped by Name Resolver
recurrent platinum-sensitive ovarian cancer unable to be mapped by Name Resolver
high risk non-cardiac surgery unable to be mapped by Name Resolver
elderly patients undergoing spinal surgery unable to be mapped by Name Resolver
post-stroke arm spasticity unable to be mapped by Name Resolver
colon cleansing unable to be mapped by Name Resolver
non-exudative (dry) age-related macular degeneration (amd) unable to be mapped by Name Resolver
older adults (50-90 years) unable to be mapped by Name Resolver
orthopedic complications in cerebral palsy unable to be mapped by Name Resolver
three vessel coronary artery disease unable to be mapped by Name Resolver
advanced or inoperable malignant melanoma with braf mutation unable to be mapped by Name Resolver
dermal irritation unable to be mapped by Name Resolver
post operative sore throat after lma removal unable to be mapped by Name Resolver
influenza due to influenza a virus subtype h5n

advanced gastric cancer unable to be mapped by Name Resolver
ureaplasma/mycoplasma positive unable to be mapped by Name Resolver
stroke technique unable to be mapped by Name Resolver
describe novel approach to brachial plexus anesthesia unable to be mapped by Name Resolver
refractory malignant ascites unable to be mapped by Name Resolver
rhinoplasty techniques unable to be mapped by Name Resolver
end stage renal disease and kidney transplantation unable to be mapped by Name Resolver
heavy drinking days unable to be mapped by Name Resolver
high grade serous ovarian cancer unable to be mapped by Name Resolver
patients with breast cancer requiring mastectomy and suitable for reconstruction unable to be mapped by Name Resolver
bowel preparation for colonoscopy unable to be mapped by Name Resolver
immune function in blood unable to be mapped by Name Resolver
liver function in blood unable to be mapped by Name Resolver
variation of ascites unable to be mapped by Name Resolver
characters of q

complications of atrial fibrillation unable to be mapped by Name Resolver
children receiving ventilation at home for chronic illness or disease unable to be mapped by Name Resolver
coronary heart disease not otherwise specified unable to be mapped by Name Resolver
subarachnoid haemorrhagic stroke unable to be mapped by Name Resolver
intracerebral haemorrhagic stroke unable to be mapped by Name Resolver
stroke not otherwise specified unable to be mapped by Name Resolver
unheralded coronary death unable to be mapped by Name Resolver
fatal cardiovascular disease (fatal cvd) unable to be mapped by Name Resolver
myocardial infarction not otherwise specified (mi nos) unable to be mapped by Name Resolver
repeated ivf failure unable to be mapped by Name Resolver
deferred umbilical cord clamping unable to be mapped by Name Resolver
temporary abdominal closure mechanisms unable to be mapped by Name Resolver
preterm birth recurrence unable to be mapped by Name Resolver
locally advanced or metasta

hyperglycemia in pregnant diabetic patients unable to be mapped by Name Resolver
left-sided pancreatic cancer unable to be mapped by Name Resolver
unipolar major depressive disorder unable to be mapped by Name Resolver
surgical technical skill unable to be mapped by Name Resolver
technical errors in surgery unable to be mapped by Name Resolver
therapeutics of bilateral maxillofacial injuries unable to be mapped by Name Resolver
latent tuberculosis infection (lti) unable to be mapped by Name Resolver
polypharmacy because of multimorbidity in geriatric nursing home residents unable to be mapped by Name Resolver
patients with traumatic pain, post-surgical pain and tooth extract pain unable to be mapped by Name Resolver
consecutive incident adult patients undergoing elective cardiac surgery unable to be mapped by Name Resolver
inherited retinal dystrophies unable to be mapped by Name Resolver
stage 4 breast cancer unable to be mapped by Name Resolver
chronic heart failure with reduced ejec

...

joint disease secondary to osteoarthritis unable to be mapped by Name Resolver
chordoma (poorly differentiated or de-differentiated) unable to be mapped by Name Resolver
other ini1 negative tumors (with pi approval) unable to be mapped by Name Resolver
other smarca4-deficient malignant tumors (with pi approval) unable to be mapped by Name Resolver
nummular headache unable to be mapped by Name Resolver
stenosis in saphenous vein graft, drug eluting stent unable to be mapped by Name Resolver
locally advanced (unresectable) or metastatic solid tumor malignancies unable to be mapped by Name Resolver
unresectable or metastatic colorectal cancer unable to be mapped by Name Resolver
ttr-cm unable to be mapped by Name Resolver
melatonin production unable to be mapped by Name Resolver
dysmorphic uterus unable to be mapped by Name Resolver
patch,chinese herb unable to be mapped by Name Resolver
unresectable or metastatic microsatellite stable (mss) solid tumor along with microsatellite stable (m

epidermotropic t-cell lymphomas unable to be mapped by Name Resolver
pediatric thoracoscopy unable to be mapped by Name Resolver
pharmacokinetics and safety of elevated doses unable to be mapped by Name Resolver
metastatic solid tumors, refractory/relapsed hematologic malignancies unable to be mapped by Name Resolver
wear of denture teeth unable to be mapped by Name Resolver
minor intra-uterine abnormalities unable to be mapped by Name Resolver
severe forms of hemophilia unable to be mapped by Name Resolver
other constitutional bleeding disorders unable to be mapped by Name Resolver
preoperative systemic treatment unable to be mapped by Name Resolver
childbirth fear, anxiety,birth pain unable to be mapped by Name Resolver
patients with metabolic syndrome unable to be mapped by Name Resolver
patients indicated for an icd unable to be mapped by Name Resolver
chinese mothers unable to be mapped by Name Resolver
catheter associated urinary tract infections unable to be mapped by Name Resol

agitation associated with bipolar disorder unable to be mapped by Name Resolver
osteosynthesis or conservative treatment unable to be mapped by Name Resolver
systemic inflammatory stress response unable to be mapped by Name Resolver
stage ii a/b seminomatous germ cell tumors unable to be mapped by Name Resolver
community-dwelling elderly unable to be mapped by Name Resolver
maternal gbs carriage unable to be mapped by Name Resolver
recreational cannabis use unable to be mapped by Name Resolver
mesenchymal stem cell-derived bioactivator for treating chronic wounds unable to be mapped by Name Resolver
nasal carriage of staphylococcus aureus unable to be mapped by Name Resolver
suicidal behaviour disorder unable to be mapped by Name Resolver
locally advanced solid tumours unable to be mapped by Name Resolver
metastatic solid tumours unable to be mapped by Name Resolver
hemophilia b, congenital unable to be mapped by Name Resolver
comparing antibiotic duration of therapy unable to be mappe

postmenopausal diabetes unable to be mapped by Name Resolver
elevated lipoprotein(a) levels unable to be mapped by Name Resolver
residents's frailty in temporary accommodation unable to be mapped by Name Resolver
residents's quality of life in temporary accommodation unable to be mapped by Name Resolver
general anesthesia induced hypotension unable to be mapped by Name Resolver
oxytocin effect on memory performance during phase 1 unable to be mapped by Name Resolver
oxytocin effect on memory performance during phase 2 unable to be mapped by Name Resolver
oxytocin effect on memory performance during phase 3 unable to be mapped by Name Resolver
oxytocin effect on memory performance during phase 4 unable to be mapped by Name Resolver
autosomal dominant hypocalcemia or primary hypoparathyroidism related to other cause but complicated by hypercalciuria under treatment unable to be mapped by Name Resolver
covid-19 (severe coronavirus disease 2019) unable to be mapped by Name Resolver
infanti

clinic hip osteoarthrosis unable to be mapped by Name Resolver
gait impairment due to mild/moderate multiple sclerosis (ms) unable to be mapped by Name Resolver
other specified risk factors in pregnancy unable to be mapped by Name Resolver
multiple sclerosis, osteoporosis unable to be mapped by Name Resolver
patients suspected for a pancreatic (pre-)malignancy unable to be mapped by Name Resolver
cd22+ relapsed/refractory b-all unable to be mapped by Name Resolver
tetraplegia c5-c6 unable to be mapped by Name Resolver
locally advanced and unresectable, but non-metastatic pancreatic adenocarcinoma or cholangiocarcinoma unable to be mapped by Name Resolver
untreated metastatic pancreatic ductal adenocarcinoma unable to be mapped by Name Resolver
children exposed to adverse experiences unable to be mapped by Name Resolver
melanoma (excluding uveal melanoma) unable to be mapped by Name Resolver
high energy midshaft clavicle fractures unable to be mapped by Name Resolver
vitamin d or placeb

In [55]:
nr_terms

[{'rehabilitation': ['UMLS:C0007237', 'rehabilitation']},
 {'ovarian cancer': ['MONDO:0005140', 'Ovarian Cancer']},
 {'healthy': ['UMLS:C3898900', 'Healthy']},
 {'her2-positive gastric cancer': ['UMLS:C1868895',
   'HER2 positive gastric cancer']},
 {'neuromuscular; disorder, hereditary': ['UMLS:C1408156',
   'neuromuscular; disorder, hereditary']},
 {'radiation enteritis': ['UMLS:C0259795', 'enteritis radiation']},
 {'vertebral lesion': ['UMLS:C0877400', 'Vertebral lesion']},
 {'cerebral circulatory failure': ['UMLS:C0854112',
   'Cerebral circulatory failure']},
 {'torsades de pointe caused by drug': ['UMLS:C4510938',
   'Torsades de pointe caused by drug']},
 {'metastases to bone': ['UMLS:C0153690', 'Metastases to bone']}]

In [63]:
# with open('nr_terms.pickle', 'wb') as handle:
#     pickle.dump(nr_terms, handle, protocol=pickle.HIGHEST_PROTOCOL)

with open('nr_terms.pickle', 'rb') as handle:
    nr_terms_ = pickle.load(handle)
len(nr_terms_)


In [71]:
# get the list of terms still remaining unmapped after running SRI Name Resolver (NR)
conditions_unmapped_list = conditions_unmapped.downcase_name.unique() # get the original list of unmapped conditions
keys_set = set().union(*[d.keys() for d in nr_terms_])  # get all the keys from the list of dictionaries of terms mapped by NR
conditions_unmapped_postnr = [element for element in conditions_unmapped_list if element not in keys_set] # find the diff/list of conditions in the original list that are absent in the keys of the list of dicts (made by calling NR) 


In [74]:
len(conditions_unmapped_postnr)

36912

# Use MetaMap to try to get CUIs for remaining conditions

In [77]:
CAS_SERVERURL = "https://utslogin.nlm.nih.gov/cas/v1"
II_SKR_SERVERURL = 'https://ii.nlm.nih.gov/cgi-bin/II/UTS_Required'
METAMAP_INTERACTIVE_URL = II_SKR_SERVERURL + "/API_MM_interactive.pl"
stserverurl = "https://utslogin.nlm.nih.gov/cas/v1/tickets"
tgtserverurl = "https://utslogin.nlm.nih.gov/cas/v1/api-key"
apikey = '54041f07-fc66-4558-b038-b46ca8bdcc6b'
serviceurl = METAMAP_INTERACTIVE_URL
ksource = '2020AB'

def get_service_ticket(serverurl, ticket_granting_ticket, serviceurl):
    """ Obtain a Single-Use Proxy Ticket (also known as service ticket).
    Request for a Service Ticket:
        POST /cas/v1/tickets/{TGT id} HTTP/1.0
    data:
           service={form encoded parameter for the service url}
    Sucessful Response:
        200 OK
        ST-1-FFDFHDSJKHSDFJKSDHFJKRUEYREWUIFSD2132
    @param serverurl authentication server
    @param ticketGrantingTicket a Proxy Granting Ticket.
    @param serviceurl url of service with protected resources
    @return authentication ticket for service. """
    resp = requests.post("{}/{}".format(serverurl, ticket_granting_ticket),
                         {"service": serviceurl})
    if resp.status_code == 200:
        return resp.content
    return 'Error: status: {}'.format(resp.content)


def extract_tgt_ticket(htmlcontent):
    "Extract ticket granting ticket from HTML."
    # print('htmlcontent: {}'.format(htmlcontent))
    html = HTML(html=htmlcontent)
    # get form element
    elements = html.xpath("//form")
    # print('html response: {}'.format(etree.tostring(html.lxml).decode()))
    # print('action attribure: {}'.format(elements[0].attrs['action']))
    # extract ticket granting ticket out of 'action' attribute
    if elements != []:
        return elements[0].attrs['action'].split('/')[-1]
    else:
        return "form element missing from ticket granting ticket response"

def get_ticket(cas_serverurl, apikey, serviceurl):
    # set ticket granting ticket server url
    tgtserverurl = cas_serverurl + "/api-key"
    # set service ticket server url
    stserverurl = cas_serverurl + "/tickets"
    tgt = get_ticket_granting_ticket(tgtserverurl, apikey)
    return get_service_ticket(stserverurl, tgt, serviceurl)

def get_ticket_granting_ticket(tgtserverurl, apikey):
    # http://serviceurl/cas/v1/tickets/{TGT id}
    response = requests.post(tgtserverurl, {'apikey': apikey},
                             headers={'Accept': 'test/plain'})
    return extract_tgt_ticket(response.content)

def extract_tgt_ticket(htmlcontent):
    "Extract ticket granting ticket from HTML."    
    soup = BeautifulSoup(htmlcontent)
#     print(soup.find('form').get("action"))
    cas_url = soup.find("form").get("action")
    "Extract ticket granting ticket out of 'action' attribute"
#     tgt = cas_url.rsplit('/')[-1]
    return cas_url.rsplit('/')[-1]
    
ticket = get_ticket(CAS_SERVERURL, apikey, serviceurl)


In [78]:
args = ['-I -i -z -C']
form = {}
form['APIText'] = "A spinal tap was performed and oligoclonal bands were \
detected in the cerebrospinal fluid.\n"
form['KSOURCE'] = ksource
form['COMMAND_ARGS'] = args
serviceticket = ticket
params = {'ticket': serviceticket}
headers = {'Accept': 'application/json'}
s = requests.Session()
response = s.post(serviceurl, form, headers=headers, params=params, allow_redirects=False)

In [79]:
def get_redirect_target(resp):
        """Receives a Response. Returns a redirect URI or ``None``"""
        # Due to the nature of how requests processes redirects this method will
        # be called at least once upon the original response and at least twice
        # on each subsequent redirect response (if any).
        # If a custom mixin is used to handle this logic, it may be advantageous
        # to cache the redirect location onto the response object as a private
        # attribute.
        if resp.is_redirect:
            location = resp.headers["location"]
            # Currently the underlying http module on py3 decode headers
            # in latin1, but empirical evidence suggests that latin1 is very
            # rarely used with non-ASCII characters in HTTP headers.
            # It is more likely to get UTF8 header rather than latin1.
            # This causes incorrect handling of UTF8 encoded location headers.
            # To solve this, we re-encode the location in latin1.
#             print(location)
            location = location.encode("latin1")
#             print(location)
#             print(to_native_string(location, "utf8"))
            return to_native_string(location, "utf8")
        return None

if response.status_code == 302:
    newurl = s.get_redirect_target(response)
    response = s.post(newurl, form, headers=headers, params=params, allow_redirects=False)

In [316]:
def split_list_by_length(lst):
    result = []
    current_sublist = []
    current_length = 0
    for item in lst:
        item_length = len(item)
        if current_length + item_length > 9000: # max is 10,000 char allowed by MetaMap
            result.append(current_sublist)
            current_sublist = []
            current_length = 0
        item = item + "\n"  # add a "\n" for term processing option by MetaMap, the terms in the input file must be separated by blank lines (https://lhncbc.nlm.nih.gov/ii/tools/MetaMap/Docs/TermProcessing.pdf)
        current_sublist.append(item)
        current_length += item_length
    result.append(current_sublist)
    return result

In [317]:
conditions_unmapped_postnr_chunked = split_list_by_length(conditions_unmapped_postnr)
conditions_unmapped_postnr_chunked[:1]


[['e03.155.197\n',
  'advanced solid tumors\n',
  'locally advanced or metastatic digestive tract tumors\n',
  'other solid tumors\n',
  'need for tracheal tube exchange\n',
  'primary total hip replacement (thr)\n',
  'presence of post-extubation laryngeal oedema\n',
  'any medical condition presented by patient\n',
  'abdominothoracic surgery\n',
  'village children\n',
  'hospitalized smokers\n',
  'patients in highest medication error risk\n',
  'unexplained subfertile couples with a good prognosis.\n',
  'posterior capsule opacification after phacoemulsification and iol implantation\n',
  'gastrointestinal bleedings\n',
  'méléna\n',
  'severe alcoholic hepatitis\n',
  'non-small cell lunch cancer\n',
  'assessment of muscle architecture and tendon after chronic stretching program\n',
  'non st-elevation acute coronary syndromes\n',
  'buprenorphine withdrawal syndrome\n',
  'conditions: serious mental illness\n',
  'growth and tolerance infant study\n',
  'adult acute myeloid leu

In [287]:
condition_args = ['--sldi -I -C -J acab,anab,cgab,comd,dsyn,inpo,mobd,neop,patf,sosy -z -i -f']  # see https://lhncbc.nlm.nih.gov/ii/tools/MetaMap/Docs/SemanticTypes_2018AB.txt for semantic types ("acab,anab,etc.")
intervention_args = ['--sldi -i -I -C -z -f -J aapp, acty, antb, bacs, bact, bdsu, bhvr, chem, chvf, chvs, clnd, cnce, diap, dora, drdd, edac, elii, enty, enzy, fngs, food, ftcn, genf, gngm, hcpp, hlca, hops, horm, idcn, imft, inbe, inch, inpo, inpr, irda, lang, lbpr, lbtr, mbrt, mcha, medd, menp, mnob, moft, nnon, npop, ocac, ocdi, orch, phob, phpr, phsu, plnt, qlco, qnco, rcpt, resa, resd, sbst, socb, spco, tmco, topp, virs, vita']  # see https://lhncbc.nlm.nih.gov/ii/tools/MetaMap/Docs/SemanticTypes_2018AB.txt for semantic types ("acab,anab,etc.")

form = {}
form['KSOURCE'] = ksource
form['COMMAND_ARGS'] = condition_args
# form['COMMAND_ARGS'] = intervention_args
headers = {'Accept': 'application/json'}

mm_terms = {}
cui_pattern = r"C\d+(?=:)"
name_pattern = r"(?<=:)[^[]+"
semtype_pattern = r"\[(.*?)\]"

# for chunk in conditions_unmapped_postnr_chunked[:2]: # demo for testing
for chunk in conditions_unmapped_postnr_chunked:
    service_ticket = get_ticket(CAS_SERVERURL, apikey, serviceurl)
#     chunk = chunk[:4] # demo for testing
    chunk = "\n".join(chunk)

    form['APIText'] = chunk
    params = {'ticket': service_ticket}
    
    trycnt = 5  # max try count to recieve response from MetaMap Interactive Server
    while trycnt > 0:
        try:
            response = s.post(serviceurl, form, headers=headers, params=params, allow_redirects=False)
            if response.status_code == 302:
                newurl = s.get_redirect_target(response)
                response = s.post(newurl, form, headers=headers, params=params, allow_redirects=False)
            trycnt = 0 # success, recieved response from MetaMap Interactive Server
        except (ConnectionResetError,OSError) as ex:  # Catch ProtocolError or socket.error in requests that raises a ConnectionError as "OSError" ....https://stackoverflow.com/questions/74253820/cannot-catch-requests-exceptions-connectionerror-with-try-except
            if trycnt <= 0: print("Failed to retrieve MetaMap response\n" + str(ex))  # done retrying
            else: trycnt -= 1  # retry
            time.sleep(5)  # wait 5 second then retry

#     print(response.text)
    
    for line in response.text.splitlines():
        if not any(s in line for s in ["Meta Mapping", "Processing", "/dmzfiler/"]):
            if "Phrase:" in line:
                cuis_per_input = []
                mm_input = line.split(":")[1].strip()
                cui_match_count = 0
            else:
                cui_match = re.findall(cui_pattern, line)
                if cui_match: 
                    cui_match_count +=1
                    if cui_match_count > 1: # get only 1st CUI/CURIE per Phrase; continue to next loop iteration to skip lines with more available CUIs
                        continue
                    cui_info = []
                    name_match = re.findall(name_pattern, line)
                    semtype_match = re.findall(semtype_pattern, line)
                    try:
                        cui_info.append(cui_match[0].strip())
                    except: cui_info.append(None)
                    try:
                        cui_info.append(name_match[0].strip())
                    except: cui_info.append(None)
                    try:
                        cui_info.append(semtype_match[0].strip())
                    except: cui_info.append(None)
                    cuis_per_input.append(cui_info)
                    mm_terms[mm_input] = cuis_per_input
      

In [288]:
# with open('mm_terms.pickle', 'wb') as handle:
#     pickle.dump(mm_terms, handle, protocol=pickle.HIGHEST_PROTOCOL)

with open('nr_terms.pickle', 'rb') as handle:
    mm_terms_ = pickle.load(handle)
len(mm_terms)

19288

In [ ]:
condition_args = ['--sldi -I -C -J acab,anab,cgab,comd,dsyn,inpo,mobd,neop,patf,sosy -z -i -f']  # see https://lhncbc.nlm.nih.gov/ii/tools/MetaMap/Docs/SemanticTypes_2018AB.txt for semantic types ("acab,anab,etc.")
intervention_args = ['--sldi -i -I -C -z -f -J aapp, acty, antb, bacs, bact, bdsu, bhvr, chem, chvf, chvs, clnd, cnce, diap, dora, drdd, edac, elii, enty, enzy, fngs, food, ftcn, genf, gngm, hcpp, hlca, hops, horm, idcn, imft, inbe, inch, inpo, inpr, irda, lang, lbpr, lbtr, mbrt, mcha, medd, menp, mnob, moft, nnon, npop, ocac, ocdi, orch, phob, phpr, phsu, plnt, qlco, qnco, rcpt, resa, resd, sbst, socb, spco, tmco, topp, virs, vita']  # see https://lhncbc.nlm.nih.gov/ii/tools/MetaMap/Docs/SemanticTypes_2018AB.txt for semantic types ("acab,anab,etc.")

form = {}
form['KSOURCE'] = ksource
form['COMMAND_ARGS'] = condition_args
# form['COMMAND_ARGS'] = intervention_args
headers = {'Accept': 'application/json'}

mm_terms = {}
cui_pattern = r"C\d+(?=:)"
name_pattern = r"(?<=:)[^[]+"
semtype_pattern = r"\[(.*?)\]"

In [324]:
def get_metamap_response(chunk):
    mm_terms = {}
    form['APIText'] = chunk
    service_ticket = get_ticket(CAS_SERVERURL, apikey, serviceurl)
    params = {'ticket': service_ticket}

    trycnt = 5  # max try count to recieve response from MetaMap Interactive API
    while trycnt > 0:
        try:
            response = s.post(serviceurl, form, headers=headers, params=params, allow_redirects=False)
            if response.status_code == 302:
                newurl = s.get_redirect_target(response)
                response = s.post(newurl, form, headers=headers, params=params, allow_redirects=False)
            trycnt = 0 # success, recieved response from MetaMap Interactive Server
        except (ConnectionResetError,OSError) as ex:  # Catch ProtocolError or socket.error in requests that raises a ConnectionError as "OSError" ....https://stackoverflow.com/questions/74253820/cannot-catch-requests-exceptions-connectionerror-with-try-except
            if trycnt <= 0: print("Failed to retrieve MetaMap response\n" + str(ex))  # done retrying
            else: trycnt -= 1  # retry
            time.sleep(5)  # wait 5 second then retry
            
    for line in response.text.splitlines():
        if not any(s in line for s in ["Meta Mapping", "Processing", "/dmzfiler/"]):
            if "Phrase:" in line:
                cuis_per_input = []
                mm_input = line.split(":")[1].strip()
                cui_match_count = 0
            else:
                cui_match = re.findall(cui_pattern, line)
                if cui_match: 
                    cui_match_count +=1
                    if cui_match_count > 1: # get only 1st CUI/CURIE per Phrase; continue to next loop iteration to skip lines with more available CUIs
                        continue
                    cui_info = []
                    name_match = re.findall(name_pattern, line)
                    semtype_match = re.findall(semtype_pattern, line)
                    try:
                        cui_info.append(cui_match[0].strip())
                    except: cui_info.append(None)
                    try:
                        cui_info.append(name_match[0].strip())
                    except: cui_info.append(None)
                    try:
                        cui_info.append(semtype_match[0].strip())
                    except: cui_info.append(None)
                    cuis_per_input.append(cui_info)
                    mm_terms[mm_input] = cuis_per_input
    return mm_terms


In [326]:

with ThreadPool(4) as pool: # 4 requests to run in parallel
    output = pool.map(get_metamap_response, conditions_unmapped_postnr_chunked)
merged_mm_dict = reduce(lambda d1, d2: {**d1, **d2}, output)

ValueError: dictionary update sequence element #0 has length 21; 2 is required

In [339]:
n_cores_use = multiprocessing.cpu_count() - 1
n_cores_use

3

# MetaMap local installation use

In [ ]:
# Setup UMLS Server global vars

global metamap_pos_server_dir
global metamap_wsd_server_dir
metamap_pos_server_dir = 'bin/skrmedpostctl'
metamap_wsd_server_dir = 'bin/wsdserverctl'
vocab_restriction = ['SNOMEDCT_US', 'SNOMEDCT_VET', 'ICD10CM', 'ICD10CM', 'ICD10PCS', 'ICD9CM', 'ICD9CM']

def check_os():
    if "linux" in sys.platform:
        print("Linux platform detected")
        metamap_base_dir = "{}/metamap/".format(pathlib.Path.cwd().parents[0])
        metamap_bin_dir = 'bin/metamap20'
    else:
        metamap_base_dir = '/Volumes/TOSHIBA_EXT/ISB/clinical_trials/public_mm/' # for running on local
        metamap_bin_dir = 'bin/metamap18'
        
    return {"metamap_base_dir":metamap_base_dir, "metamap_bin_dir":metamap_bin_dir}
        
metamap_dirs = check_os()
metamap_dirs['metamap_bin_dir']

# /Volumes/TOSHIBA_EXT/ISB/clinical_trials/public_mm

def start_metamap_servers(metamap_dirs):
    # Start servers
    os.system(metamap_dirs['metamap_base_dir'] + metamap_pos_server_dir + ' start') # Part of speech tagger
    os.system(metamap_dirs['metamap_base_dir'] + metamap_wsd_server_dir + ' start') # Word sense disambiguation 
    # # Sleep a bit to give time for these servers to start up
    sleep(60)

def stop_metamap_servers(metamap_dirs):
    # Stop servers
    os.system(metamap_dirs['metamap_base_dir'] + metamap_pos_server_dir + ' stop') # Part of speech tagger
    os.system(metamap_dirs['metamap_base_dir'] + metamap_wsd_server_dir + ' stop') # Word sense disambiguation 
        

In [ ]:
def preprocess_cols(ct_final, metamap_dirs):
    # prep a list to hold dicts of de-asciied cols from the ClinTrials df
    transformations = {}

    # get unique lists of the concepts to MetaMap from the ClinTrials df
    conditions = list(ct_final['subject_name'].unique())
    conditions = [x for x in conditions if pd.isnull(x) == False]
    interventions = list(ct_final['object_name'].unique())
    interventions = [x for x in interventions if pd.isnull(x) == False]
    
    # report the number of unique conditions and interventions to get idea of KG at early stage
    print("# of unique CONDITIONS present in Clinical Trials dataset: {}".format(len(conditions)))
    print("# of unique INTERVENTIONS present in Clinical Trials dataset: {}".format(len(interventions)))
    
    # only remove non-ASCII for MetaMap versions prior to 2020 release
    # if stmnt is checking if 20 for 2020 ---> bin/metamap20 is MetaMap release 2020
    metamap_version = [int(s) for s in re.findall(r'\d+', metamap_dirs.get('metamap_bin_dir'))]
    if metamap_version[0] >= 20:
        print("MetaMap version >= 2020, will not remove ")
        conditions_unchanged = dict((i, i) for i in conditions)
        interventions_unchanged = dict((i, i) for i in interventions) 
        transformations["conditions"] = conditions_unchanged
        transformations["interventions"] = interventions_unchanged      
    else:
        print("Removing ASCII char from cols.")
        print("This step is unnecessary for MetaMap 2020+")
        conditions_translated = dict((i, de_ascii_er(i)) for i in conditions)
        interventions_translated = dict((i, de_ascii_er(i)) for i in interventions)   
        
        transformations["conditions"] = conditions_translated
        transformations["interventions"] = interventions_translated  
        
    return(transformations)
        

transformed = preprocess_cols(ct_final, metamap_dirs)


In [ ]:
stop_metamap_servers(metamap_dirs)

In [ ]:
def driver():
    metamap_dirs = check_os()
    flag_and_path = get_raw_ct_data()
    
    if flag_and_path.get("term_program_flag"):
        print("Exiting")
        quit()
    else:
        ct_data = merge_raw_ct_data(flag_and_path.get("data_extracted_path"))
        ct_final = preprocess_ct_data(ct_data)
#         metamap_compatible_cols = select_cols(ct_final)

driver()     

### Conclusion: there are multiple candidate MeSH terms (leaf nodes only, not ancestors) available per 1 condition

# Use MetaMap to find more candidate matches

In [ ]:
CAS_SERVERURL = "https://utslogin.nlm.nih.gov/cas/v1"
II_SKR_SERVERURL = 'https://ii.nlm.nih.gov/cgi-bin/II/UTS_Required'
METAMAP_INTERACTIVE_URL = II_SKR_SERVERURL + "/API_MM_interactive.pl"
stserverurl = "https://utslogin.nlm.nih.gov/cas/v1/tickets"
tgtserverurl = "https://utslogin.nlm.nih.gov/cas/v1/api-key"
apikey = '54041f07-fc66-4558-b038-b46ca8bdcc6b'
serviceurl = METAMAP_INTERACTIVE_URL
ksource = '2020AB'

def get_service_ticket(serverurl, ticket_granting_ticket, serviceurl):
    """ Obtain a Single-Use Proxy Ticket (also known as service ticket).
    Request for a Service Ticket:
        POST /cas/v1/tickets/{TGT id} HTTP/1.0
    data:
           service={form encoded parameter for the service url}
    Sucessful Response:
        200 OK
        ST-1-FFDFHDSJKHSDFJKSDHFJKRUEYREWUIFSD2132
    @param serverurl authentication server
    @param ticketGrantingTicket a Proxy Granting Ticket.
    @param serviceurl url of service with protected resources
    @return authentication ticket for service. """
    resp = requests.post("{}/{}".format(serverurl, ticket_granting_ticket),
                         {"service": serviceurl})
    if resp.status_code == 200:
        return resp.content
    return 'Error: status: {}'.format(resp.content)


def extract_tgt_ticket(htmlcontent):
    "Extract ticket granting ticket from HTML."
    # print('htmlcontent: {}'.format(htmlcontent))
    html = HTML(html=htmlcontent)
    # get form element
    elements = html.xpath("//form")
    # print('html response: {}'.format(etree.tostring(html.lxml).decode()))
    # print('action attribure: {}'.format(elements[0].attrs['action']))
    # extract ticket granting ticket out of 'action' attribute
    if elements != []:
        return elements[0].attrs['action'].split('/')[-1]
    else:
        return "form element missing from ticket granting ticket response"

def get_ticket(cas_serverurl, apikey, serviceurl):
    # set ticket granting ticket server url
    tgtserverurl = cas_serverurl + "/api-key"
    # set service ticket server url
    stserverurl = cas_serverurl + "/tickets"
    tgt = get_ticket_granting_ticket(tgtserverurl, apikey)
    return get_service_ticket(stserverurl, tgt, serviceurl)

def get_ticket_granting_ticket(tgtserverurl, apikey):
    # http://serviceurl/cas/v1/tickets/{TGT id}
    response = requests.post(tgtserverurl, {'apikey': apikey},
                             headers={'Accept': 'test/plain'})
    return extract_tgt_ticket(response.content)

def extract_tgt_ticket(htmlcontent):
    "Extract ticket granting ticket from HTML."    
    soup = BeautifulSoup(htmlcontent)
#     print(soup.find('form').get("action"))
    cas_url = soup.find("form").get("action")
    "Extract ticket granting ticket out of 'action' attribute"
#     tgt = cas_url.rsplit('/')[-1]
    return cas_url.rsplit('/')[-1]
    
ticket = get_ticket(CAS_SERVERURL, apikey, serviceurl)

In [ ]:
def get_redirect_target(resp):
        """Receives a Response. Returns a redirect URI or ``None``"""
        # Due to the nature of how requests processes redirects this method will
        # be called at least once upon the original response and at least twice
        # on each subsequent redirect response (if any).
        # If a custom mixin is used to handle this logic, it may be advantageous
        # to cache the redirect location onto the response object as a private
        # attribute.
        if resp.is_redirect:
            location = resp.headers["location"]
            # Currently the underlying http module on py3 decode headers
            # in latin1, but empirical evidence suggests that latin1 is very
            # rarely used with non-ASCII characters in HTTP headers.
            # It is more likely to get UTF8 header rather than latin1.
            # This causes incorrect handling of UTF8 encoded location headers.
            # To solve this, we re-encode the location in latin1.
#             print(location)
            location = location.encode("latin1")
#             print(location)
#             print(to_native_string(location, "utf8"))
            return to_native_string(location, "utf8")
        return None

if response.status_code == 302:
    newurl = s.get_redirect_target(response)
    response = s.post(newurl, form, headers=headers, params=params, allow_redirects=False)

In [ ]:
# get concepts to map
conditions_unmapped.downcase_name.to_list()[:10]

In [ ]:
conditions_unmapped

In [ ]:
len(conditions_unmapped['downcase_name'].to_list())

In [ ]:
len(set(conditions_unmapped['downcase_name'].to_list()))

In [ ]:
conditions_unmapped_list = list(set(conditions_unmapped.downcase_name.to_list())) # get unique unmapped terms
conditions_unmapped_list = [s + "\r\n" for s in conditions_unmapped_list] # you must include newline to process each term separately!
print(len(conditions_unmapped_list))

In [ ]:
def split_list_by_length(lst):
    result = []
    current_sublist = []
    current_length = 0
    for item in lst:
        item_length = len(item)
        if current_length + item_length > 9990: # max is 10,000 char allowed by MetaMap
            result.append(current_sublist)
            current_sublist = []
            current_length = 0
        current_sublist.append(item)
        current_length += item_length
    result.append(current_sublist)
    return result

In [ ]:
chunked_conditions_unmapped = split_list_by_length(conditions_unmapped_list)
chunked_conditions_unmapped[:1]

In [17]:
"""
-I = return CUIs/identifiers
-i = ignore word order
-C = relaxed model
-z = term processing
-f = give numbers to the final mappings (adds 1. to the first mapped concept, 2. to the 2nd, and so on...)
-c = give numbers to the candidates (adds 1. to the first candidate, 2. to the 2nd, and so on...)
--sldi = read each term in list separately, do not lump into large phrase
-N = MMI formatted output

https://lhncbc.nlm.nih.gov/ii/tools/MetaMap/Docs/ListOfTerms.pdf
https://lhncbc.nlm.nih.gov/ii/tools/MetaMap/Docs/TermProcessing.pdf
https://lhncbc.nlm.nih.gov/ii/tools/MetaMap/Docs/MM_2016_Usage.pdf
List of MetaMap semantic types: https://lhncbc.nlm.nih.gov/ii/tools/MetaMap/Docs/SemanticTypes_2018AB.txt
"""

cwd_absolute_path = os.path.dirname(os.getcwd())
outputs_folder = "outputs/version_2"
outputs_path = os.path.join(absolute_path, outputs_folder)

# args = ['--sldi -i -I -C -z -J acab,anab,bhvr,cgab,clna,dsyn,fndg,inpo,mobd,neop,patf,sosy'] # see https://lhncbc.nlm.nih.gov/ii/tools/MetaMap/Docs/SemanticTypes_2018AB.txt for semantic types ("acab,anab,etc.")
args = ['--sldi -i -I -C -z'] # see https://lhncbc.nlm.nih.gov/ii/tools/MetaMap/Docs/SemanticTypes_2018AB.txt for semantic types ("acab,anab,etc.")
form = {}
form['KSOURCE'] = ksource
form['COMMAND_ARGS'] = args
headers = {'Accept': 'application/json'}

mm_conditions = {}
cui_pattern = r"C\d+(?=:)"
name_pattern = r"(?<=:)[^[]+"
semtype_pattern = r"\[(.*?)\]"

# with open('../outputs/version_2/metamapped_conditions_.txt') as output:
# with open(os.path.join(outputs_path, "metamapped_conditions.txt"), 'w') as output:

for chunk in chunked_conditions_unmapped[:3]: # demo for testing
    chunk = chunk[:20] # demo for testing
#     for chunk in chunked_conditions_unmapped:
    service_ticket = get_ticket(CAS_SERVERURL, apikey, serviceurl)
    form['APIText'] = chunk
    params = {'ticket': service_ticket}
    response = s.post(serviceurl, form, headers=headers, params=params, allow_redirects=False)
    if response.status_code == 302:
        newurl = s.get_redirect_target(response)
        response = s.post(newurl, form, headers=headers, params=params, allow_redirects=False)

    for line in response.text.splitlines():
#         output.write(line)
        if not any(s in line for s in ["Meta Mapping", "Processing", "/dmzfiler/"]):
#             mm_dict = {}
            if "Phrase:" in line:
                cuis_per_input = []
                mm_input = line.split(":")[1].strip()
                print(mm_input)
            else:
                cui_match = re.findall(cui_pattern, line)
                if cui_match:
                    name_match = re.findall(name_pattern, line)
                    semtype_match = re.findall(semtype_pattern, line)
                    cui_info = [cui_match[0].strip(), name_match[0].strip(), semtype_match[0].strip()]
                    cuis_per_input.append(cui_info)    

                mm_conditions[mm_input] = cuis_per_input
    
mm_conditions


NameError: name 'absolute_path' is not defined

In [ ]:
conditions_unmapped_list = list(set(conditions_unmapped.downcase_name.to_list())) # get unique unmapped terms
conditions_unmapped_list[:100]

In [ ]:
conditions_unmapped_list = list(set(conditions_unmapped.downcase_name.to_list())) # get unique unmapped terms
nr_url = 'https://name-resolution-sri.renci.org/lookup'

nr_dict =  {}
for condition in conditions_unmapped_list[:3]:
    params = {'string':condition,'limit':3}
    response = requests.post(nr_url,params=params)
#     print(response.json())
#     print(json.dumps(response.json(),indent=2))
    jres = response.json()
#     print(jres)
#     jres = json.load(res)
    nr_dict[condition] = jres
    
    
nr_dict

In [ ]:
diseases = ['planned rrso', 'human bocavirus', 'articular cartilage defects of knee', 'pustular psoriasis', 'chronic migraine headache']

params = {'string':diseases,'limit':5}
response = requests.post(nr_url,params=params)
print(json.dumps(response.json(),indent=2))


In [ ]:
diseases = ['planned rrso', 'human bocavirus', 'articular cartilage defects of knee', 'pustular psoriasis', 'chronic migraine headache']

params = {'string':"RxCUI 2555",'limit':5}
response = requests.post(nr_url,params=params)
print(json.dumps(response.json(),indent=2))

In [ ]:
with open(os.path.join(outputs_path, "metamapped_conditions.txt"), 'w') as output:
    for key, val in mm_conditions.items():
        print(key)
#             output.write(key + "\t" + val[0] + "\t" + val[1] + "\t" + val[2])


In [ ]:
mm_conditions